In [25]:
import pandas as pd
import plotly.graph_objects as go
import shared

pd.options.plotting.backend = "plotly"
pd.set_option('display.max_columns', None)

# it's important to define index and parse_dates
landkreise = pd.read_csv('data/inf_lk.csv', sep=',', index_col=0, parse_dates=True)
lander = pd.read_csv('data/inf_bl.csv', sep=',', index_col=0, parse_dates=True)

palette = shared.get_palette()

In [26]:
last_updated_string = str(lander.tail(1).index.values[0])[0:10]

html_string = f'<!DOCTYPE html PUBLIC"ISO/IEC 15445:2000//DTD HTML//EN"><html><head><title></title></head><body><p>Last Updated: {last_updated_string}</p></body></html>'
f = open("plots/last_update.html", "w")
f.write(html_string)
f.close()


In [27]:
ags_df = pd.read_json('data/ags.json').transpose()


def get_ags(lk_name):
    row = ags_df[ags_df['name'] == lk_name]
    return f'{row.index.values[0]}'


def get_lk_pop(lk_name):
    row = ags_df[ags_df['name'] == lk_name]
    return row.population.values[0]


# get land pop can be found in shared.py

# get state of lankkreis
def get_state(lk_name):
    row = ags_df[ags_df['name'] == lk_name]
    return row.state.values[0]


ags_df[ags_df['name'] == 'SK München']

name   state      lat      lon population note
9162  SK München  Bayern  48.1374  11.5755    1484226  NaN

In [28]:
lander.head(3)

DE-BB  DE-BE  DE-BW  DE-BY  DE-HB  DE-HE  DE-HH  \
time_iso8601                                                                 
2020-03-03 20:00:00+00:00      1      9     65     70      3     12      5   
2020-03-04 20:00:00+00:00      1      9     65     70      3     12      5   
2020-03-05 20:00:00+00:00      1     15     91     91      3     12      6   

                           DE-MV  DE-NI  DE-NW  DE-RP  DE-SH  DE-SL  DE-SN  \
time_iso8601                                                                 
2020-03-03 20:00:00+00:00      4      9    179      6      5      1      1   
2020-03-04 20:00:00+00:00      4      9    179      6      5      1      1   
2020-03-05 20:00:00+00:00      5     18    304      9      7      1      1   

                           DE-ST  DE-TH  sum_cases  
time_iso8601                                        
2020-03-03 20:00:00+00:00      0      1        371  
2020-03-04 20:00:00+00:00      0      1        371  
2020-03-05 20:00:00+00:00      0      1        565

In [29]:
def trend(x):
    if x < -0.05:
        return 'DOWN_STRONG'
    elif x < -0.01:
        return 'DOWN'
    elif x < 0.01:
        return 'STEADY'
    elif x < 0.05:
        return 'UP'
    else:
        return 'UP_STRONG'

def week_inz_lk(grouped_df, year_and_week):
    return round(grouped_df.loc[year_and_week, 'inz'],2)

def prepare_lk(lk_name):
    lk = landkreise[get_ags(lk_name)].to_frame()
    lk = lk.rename(columns={f"{get_ags(lk_name)}": "inf_sum"})

    lk['dif'] = lk.inf_sum - lk.inf_sum.shift(1)
    lk['dif'] = lk['dif'].fillna(0)
    lk = lk.astype({'dif': 'int64'})

    lk['rolling_dif'] = lk.dif.rolling(7).mean()

    lk['inf_7_tage'] = lk.inf_sum - lk.inf_sum.shift(7)
    lk['inf_7_tage'] = lk['inf_7_tage'].fillna(method='bfill')
    lk = lk.astype({'inf_7_tage': 'int64'})

    lk['inz'] = round(lk['inf_7_tage'] / (get_lk_pop(lk_name) / 100_000), 1)

    lk['inz_dif'] = (lk['inz'] - lk['inz'].shift(1))
    lk['inz_trend'] = round(lk['inz_dif'] / lk.inz, 2)
    lk['inz_trend'] = lk.apply(lambda x: trend(x['inz_trend']), axis=1)

    lk['date'] = lk.index
    lk = shared.add_weekday_stuff(lk, 'date')
    grouped = lk.groupby(['year_and_week']).mean()
    lk['week_inz'] = lk.apply(lambda x: week_inz_lk(grouped, x['year_and_week']), axis=1)

    return lk


In [30]:
lk_name = 'SK München'
print(f'{lk_name} Einwohnerzahl: {get_lk_pop(lk_name)}')
print(f'{lk_name} Einwohnerzahl durch 100.000 {get_lk_pop(lk_name) / 100_000}')
debug = prepare_lk(lk_name)
debug.tail(14)

SK München Einwohnerzahl: 1484226
SK München Einwohnerzahl durch 100.000 14.84226


inf_sum   dif  rolling_dif  inf_7_tage    inz  \
time_iso8601                                                               
2021-12-31 17:00:00+00:00   144783   429   495.142857        3466  233.5   
2022-01-01 17:00:00+00:00   144789     6   494.428571        3461  233.2   
2022-01-02 17:00:00+00:00   145413   624   523.142857        3662  246.7   
2022-01-03 17:00:00+00:00   146233   820   547.142857        3830  258.0   
2022-01-04 17:00:00+00:00   147313  1080   612.714286        4289  289.0   
2022-01-05 17:00:00+00:00   148652  1339   713.000000        4991  336.3   
2022-01-06 17:00:00+00:00   149949  1297   799.285714        5595  377.0   
2022-01-07 17:00:00+00:00   151423  1474   948.571429        6640  447.4   
2022-01-08 17:00:00+00:00   152508  1085  1102.714286        7719  520.1   
2022-01-09 17:00:00+00:00   153532  1024  1159.857143        8119  547.0   
2022-01-10 17:00:00+00:00   155187  1655  1279.142857        8954  603.3   
2022-01-11 17:00:00+00:00   157303  2116  1427.142857        9990  673.1   
2022-01-12 17:00:00+00:00   159377  2074  1532.142857       10725  722.6   
2022-01-13 17:00:00+00:00   160637  1260  1526.857143       10688  720.1   

                           inz_dif  inz_trend                      date  \
time_iso8601                                                              
2021-12-31 17:00:00+00:00      4.8         UP 2021-12-31 17:00:00+00:00   
2022-01-01 17:00:00+00:00     -0.3     STEADY 2022-01-01 17:00:00+00:00   
2022-01-02 17:00:00+00:00     13.5  UP_STRONG 2022-01-02 17:00:00+00:00   
2022-01-03 17:00:00+00:00     11.3         UP 2022-01-03 17:00:00+00:00   
2022-01-04 17:00:00+00:00     31.0  UP_STRONG 2022-01-04 17:00:00+00:00   
2022-01-05 17:00:00+00:00     47.3  UP_STRONG 2022-01-05 17:00:00+00:00   
2022-01-06 17:00:00+00:00     40.7  UP_STRONG 2022-01-06 17:00:00+00:00   
2022-01-07 17:00:00+00:00     70.4  UP_STRONG 2022-01-07 17:00:00+00:00   
2022-01-08 17:00:00+00:00     72.7  UP_STRONG 2022-01-08 17:00:00+00:00   
2022-01-09 17:00:00+00:00     26.9  UP_STRONG 2022-01-09 17:00:00+00:00   
2022-01-10 17:00:00+00:00     56.3  UP_STRONG 2022-01-10 17:00:00+00:00   
2022-01-11 17:00:00+00:00     69.8  UP_STRONG 2022-01-11 17:00:00+00:00   
2022-01-12 17:00:00+00:00     49.5  UP_STRONG 2022-01-12 17:00:00+00:00   
2022-01-13 17:00:00+00:00     -2.5     STEADY 2022-01-13 17:00:00+00:00   

                           is_weekend weekday_name  calendar_week  \
time_iso8601                                                        
2021-12-31 17:00:00+00:00       False          Fri             52   
2022-01-01 17:00:00+00:00        True          Sat             52   
2022-01-02 17:00:00+00:00        True          Sun             52   
2022-01-03 17:00:00+00:00       False          Mon              1   
2022-01-04 17:00:00+00:00       False          Tue              1   
2022-01-05 17:00:00+00:00       False          Wed              1   
2022-01-06 17:00:00+00:00       False          Thu              1   
2022-01-07 17:00:00+00:00       False          Fri              1   
2022-01-08 17:00:00+00:00        True          Sat              1   
2022-01-09 17:00:00+00:00        True          Sun              1   
2022-01-10 17:00:00+00:00       False          Mon              2   
2022-01-11 17:00:00+00:00       False          Tue              2   
2022-01-12 17:00:00+00:00       False          Wed              2   
2022-01-13 17:00:00+00:00       False          Thu              2   

                          year_and_week  week_inz  
time_iso8601                                       
2021-12-31 17:00:00+00:00       2021_52    223.49  
2022-01-01 17:00:00+00:00       2021_52    223.49  
2022-01-02 17:00:00+00:00       2021_52    223.49  
2022-01-03 17:00:00+00:00       2022_01    396.40  
2022-01-04 17:00:00+00:00       2022_01    396.40  
2022-01-05 17:00:00+00:00       2022_01    396.40  
2022-01-06 17:00:00+00:00       2022_01    396.40  
2022-01-07 17:00:00+00:00       2022

In [31]:


def week_inz_bl(kurzel, grouped_df, year_and_week):
    return round(grouped_df.loc[year_and_week, f'{kurzel}_inz'],2)

def prepare_lander(df):
    for kurzel in shared.bl_kurzel:
        df[f'{kurzel}_sum'] = df[shared.inf_lander_dict[kurzel]]
        df = df.drop(columns=[shared.inf_lander_dict[kurzel]])

    # add sum_diff
    for kurzel in shared.bl_kurzel:
        df[f'{kurzel}_dif'] = df[f'{kurzel}_sum'] - df[f'{kurzel}_sum'].shift(1)
        df[f'{kurzel}_dif_7'] = df[f'{kurzel}_sum'] - df[f'{kurzel}_sum'].shift(7)
    # add inzidenz
    for kurzel in shared.bl_kurzel:
        df[f'{kurzel}_inz'] = round(df[f'{kurzel}_dif_7'] * 100_000 / shared.get_land_pop(kurzel), 2)
    # more
    df['date'] = df.index
    df = shared.add_weekday_stuff(df, 'date')
    # trend
    for kurzel in shared.bl_kurzel:
        df[f'{kurzel}_inz_dif'] = df[f'{kurzel}_inz'] - df[f'{kurzel}_inz'].shift(1)
        df[f'{kurzel}_inz_trend'] = round(df[f'{kurzel}_inz_dif'] / df[f'{kurzel}_inz'], 2)
        df[f'{kurzel}_inz_trend'] = df.apply(lambda x: trend(x[f'{kurzel}_inz_trend']), axis=1)
        
    for kurzel in shared.bl_kurzel:
        grouped = df.groupby(['year_and_week']).mean()
        df[f'{kurzel}_week_inz'] = df.apply(lambda x: week_inz_bl(kurzel, grouped, x['year_and_week']), axis=1)

    return df


lander = prepare_lander(lander)



In [32]:
grouped = lander.groupby(['year_and_week']).mean()
round(grouped.loc['2021_07', 'BY_inz'],2)

59.08

In [33]:
lander.tail(3)

BB_sum  BE_sum   BW_sum   BY_sum   DE_sum  HB_sum  \
time_iso8601                                                                   
2022-01-12 20:00:00+00:00  263014  373555  1092307  1404029  7711981   61469   
2022-01-13 20:00:00+00:00  265860  381352  1108263  1419765  7805151   63199   
2022-01-14 15:00:00+00:00  267758  388590  1108263  1430004  7831579   63199   

                           HE_sum  HH_sum  MV_sum  NI_sum   NW_sum  RP_sum  \
time_iso8601                                                                 
2022-01-12 20:00:00+00:00  521710  161544  113687  484219  1491359  301777   
2022-01-13 20:00:00+00:00  529417  165308  114969  491396  1508309  305096   
2022-01-14 15:00:00+00:00  530086  165308  114969  491988  1512406  305096   

                           SH_sum  SL_sum  SN_sum  ST_sum  TH_sum  BB_dif  \
time_iso8601                                                                
2022-01-12 20:00:00+00:00  149173   80197  675618  236409  301914  2662.0   
2022-01-13 20:00:00+00:00  153578   81078  677357  237386  302818  2846.0   
2022-01-14 15:00:00+00:00  153578   81078  677451  238236  303569  1898.0   

                           BB_dif_7  BE_dif  BE_dif_7   BW_dif  BW_dif_7  \
time_iso8601                                                               
2022-01-12 20:00:00+00:00   12344.0  8862.0   34363.0   9879.0   43828.0   
2022-01-13 20:00:00+00:00   12354.0  7797.0   36717.0  15956.0   54988.0   
2022-01-14 15:00:00+00:00   12236.0  7238.0   37993.0      0.0   49175.0   

                            BY_dif  BY_dif_7   DE_dif  DE_dif_7  HB_dif  \
time_iso8601                                                              
2022-01-12 20:00:00+00:00  12408.0   52786.0  80422.0  369769.0  1831.0   
2022-01-13 20:00:00+00:00  15736.0   61600.0  93170.0  405063.0  1730.0   
2022-01-14 15:00:00+00:00  10239.0   64928.0  26428.0  373181.0     0.0   

                           HB_dif_7  HE_dif  HE_dif_7  HH_dif  HH_dif_7  \
time_iso8601                                                              
2022-01-12 20:00:00+00:00    9442.0  7291.0   28875.0  2590.0   13769.0   
2022-01-13 20:00:00+00:00    9539.0  7707.0   32222.0  3764.0   15269.0   
2022-01-14 15:00:00+00:00    7679.0   669.0   28222.0     0.0   13258.0   

                           MV_dif  MV_dif_7  NI_dif  NI_dif_7   NW_dif  \
time_iso8601                                                             
2022-01-12 20:00:00+00:00  1348.0    6757.0  6066.0   29104.0  15833.0   
2022-01-13 20:00:00+00:00  1282.0    6838.0  7177.0   31585.0  16950.0   
2022-01-14 15:00:00+00:00     0.0    5825.0   592.0   27021.0   4097.0   

                           NW_dif_7  RP_dif  RP_dif_7  SH_dif  SH_dif_7  \
time_iso8601                                                              
2022-01-12 20:00:00+00:00   77735.0  2851.0   14493.0  3559.0   19746.0   
2022-01-13 20:00:00+00:00   81988.0  3319.0   15152.0  4405.0   20586.0   
2022-01-14 15:00:00+00:00   73577.0     0.0   12594.0     0.0   17360.0   

                           SL_dif  SL_dif_7  SN_dif  SN_dif_7  ST_dif  \
time_iso8601                                                            
2022-01-12 20:00:00+00:00   812.0    3957.0  2047.0   10701.0  1274.0   
2022-01-13 20:00:00+00:00   881.0    4138.0  1739.0   10246.0   977.0   
2022-01-14 15:00:00+00:00     0.0    3600.0    94.0    8567.0   850.0   

                           ST_dif_7  TH_dif  TH_dif_7  BB_inz   BE_inz  \
time_iso8601                                                             
2022-01-12 20:00:00+00:00    5704.0  1109.0    6165.0  489.47   936.45   
2022-01-13 20:00:00+00:00    6377.0   904.0    5464.0  489.87  1000.60   
2022-01-14 15:00:00+00:00    6098.0   751.0    5048.0  485.19  1035.38   

                           BW_inz  BY_inz  DE_inz   HB_inz  HE_inz  HH_inz  \
time_iso8601                                                                 
2022-01-12 20:00:00+00:00  394.83  402.19  444.48  1386.08  459.20  745.38  

In [34]:
def create_inz_fig():
    palette = shared.get_palette()
    fig = go.Figure()
    fig.update_layout(
        width=1050,
        height=600,
        title='Inzidenz'
    )
    return fig


def add_bl_inz(fig, lander_kurzel, smooth=1):
    for kurzel in lander_kurzel:
        name = shared.bl_dict[kurzel] if smooth == 1 else f'{shared.bl_dict[kurzel]} (Rolling {smooth} day window)'
        fig.add_trace(go.Scatter(x=lander.index,
                              y=lander[f'{kurzel}_inz'].rolling(smooth).mean(),
                              mode='lines',
                              name=name,
                              marker_color=next(palette),
                              line=dict(width=3)))
    return fig


def add_lk_inz(fig, lk_namen, smooth=1):
    for lk in lk_namen:
        lk_df = prepare_lk(lk)
        name = lk if smooth == 1 else f'{lk} (Rolling {smooth} day window)'
        fig.add_trace(go.Scatter(x=lk_df.index,
                              y=lk_df['inz'].rolling(smooth).mean(),
                              mode='lines',
                              name=name,
                              marker_color=next(palette),
                              line=dict(width=2)))
    return fig


def add_bl_cal_inz(fig, lander_kurzel):
    for kurzel in lander_kurzel:
        fig.add_trace(go.Scatter(x=lander.index,
                              y=lander[f'{kurzel}_week_inz'],
                              name=f'{shared.bl_dict[kurzel]} (Ø Woche)',
                              marker_color=next(palette),
                              line_shape='hv',
                              line=dict(dash='dot', width=2)))
    return fig


def add_lk_cal_inz(fig, lk_namen):
    for lk in lk_namen:
        lk_df = prepare_lk(lk)
        #lk_df = lk_df.groupby(['year_and_week']).mean()
        fig.add_trace(go.Scatter(x=lk_df.index,
                              y=lk_df['week_inz'],
                              name=f'{lk} (Ø Woche)',
                              marker_color=next(palette),
                              line_shape='hv',
                              line=dict(dash='dot', width=2)))
    return fig



In [35]:
fig = create_inz_fig()
fig = add_bl_inz(fig, lander_kurzel=shared.bl_kurzel)
fig.update_layout(title='Inzidenz Bundesländer')
fig.show()

In [36]:
fig = create_inz_fig()
fig = add_bl_inz(fig, lander_kurzel=['BY', 'DE'])
fig = add_lk_inz(fig, lk_namen=['SK München', 'LK München'])
fig.update_layout(title='Inzidenz München')
fig.show()

In [37]:
fig = create_inz_fig()
fig = add_bl_inz(fig, lander_kurzel=['DE'])
fig = add_lk_inz(fig,
                 lk_namen=['SK München', 'Berlin', 'SK Flensburg', 'LK Tirschenreuth', 'LK Regensburg', 'LK Miesbach'])
fig.update_layout(title='Inzidenz Bundesländer')
fig.show()


In [38]:
fig = create_inz_fig()
fig = add_bl_inz(fig, lander_kurzel=['DE'], smooth=21)
fig = add_bl_inz(fig, lander_kurzel=['DE'], smooth=7)
fig = add_bl_inz(fig, lander_kurzel=['DE'], smooth=1)
fig = add_lk_inz(fig, lk_namen=['SK München'], smooth=1)
fig = add_lk_inz(fig, lk_namen=['SK München'], smooth=7)
fig = add_lk_inz(fig, lk_namen=['SK München'], smooth=21)

fig.update_layout(title='Inzidenz')
fig.show()



In [39]:
muc_90 = prepare_lk('SK München').tail(90)


In [40]:
row = muc_90[muc_90['inz'] == min(muc_90['inz'])]
row

inf_sum  dif  rolling_dif  inf_7_tage    inz  \
time_iso8601                                                              
2021-10-16 17:00:00+00:00    90732  246   272.428571        1907  128.5   

                           inz_dif inz_trend                      date  \
time_iso8601                                                             
2021-10-16 17:00:00+00:00      3.8        UP 2021-10-16 17:00:00+00:00   

                           is_weekend weekday_name  calendar_week  \
time_iso8601                                                        
2021-10-16 17:00:00+00:00        True          Sat             41   

                          year_and_week  week_inz  
time_iso8601                                       
2021-10-16 17:00:00+00:00       2021_41    117.87

In [41]:
muc = prepare_lk('SK München').tail(365)
muc[muc.inz == muc.inz.min()]

inf_sum  dif  rolling_dif  inf_7_tage  inz  \
time_iso8601                                                            
2021-06-24 17:00:00+00:00    73434   22    19.571429         137  9.2   

                           inz_dif inz_trend                      date  \
time_iso8601                                                             
2021-06-24 17:00:00+00:00     -0.5      DOWN 2021-06-24 17:00:00+00:00   

                           is_weekend weekday_name  calendar_week  \
time_iso8601                                                        
2021-06-24 17:00:00+00:00       False          Thu             25   

                          year_and_week  week_inz  
time_iso8601                                       
2021-06-24 17:00:00+00:00       2021_25      9.77

In [42]:
muc = prepare_lk('SK München')
muc[muc.inz == muc.inz.max()]


inf_sum   dif  rolling_dif  inf_7_tage    inz  \
time_iso8601                                                               
2021-11-18 17:00:00+00:00   114592  1476  1691.428571       11840  797.7   

                           inz_dif inz_trend                      date  \
time_iso8601                                                             
2021-11-18 17:00:00+00:00     26.9        UP 2021-11-18 17:00:00+00:00   

                           is_weekend weekday_name  calendar_week  \
time_iso8601                                                        
2021-11-18 17:00:00+00:00       False          Thu             46   

                          year_and_week  week_inz  
time_iso8601                                       
2021-11-18 17:00:00+00:00       2021_46    708.93

In [43]:
muc_recent = prepare_lk('SK München').tail(50)
muc_recent[muc_recent['inz'] == max(muc_recent['inz'])]

inf_sum   dif  rolling_dif  inf_7_tage    inz  \
time_iso8601                                                               
2022-01-12 17:00:00+00:00   159377  2074  1532.142857       10725  722.6   

                           inz_dif  inz_trend                      date  \
time_iso8601                                                              
2022-01-12 17:00:00+00:00     49.5  UP_STRONG 2022-01-12 17:00:00+00:00   

                           is_weekend weekday_name  calendar_week  \
time_iso8601                                                        
2022-01-12 17:00:00+00:00       False          Wed              2   

                          year_and_week  week_inz  
time_iso8601                                       
2022-01-12 17:00:00+00:00       2022_02    679.78

In [44]:
fig = create_inz_fig()
palette = shared.get_palette()
fig = add_bl_inz(fig, ['DE','BY'])
palette = shared.get_palette()
fig = add_bl_cal_inz(fig, ['DE', 'BY'])

fig.show()

In [45]:
fig = create_inz_fig()
palette = shared.get_palette()
fig = add_bl_inz(fig, ['DE','BY'])
fig = add_lk_inz(fig, ['SK München', 'LK München', 'LK Miesbach', 'LK Tirschenreuth', 'LK Hof'])
palette = shared.get_palette()
fig = add_bl_cal_inz(fig, ['DE', 'BY'])
fig = add_lk_cal_inz(fig, ['SK München', 'LK München', 'LK Miesbach', 'LK Tirschenreuth', 'LK Hof'])
fig.update_layout(legend={'traceorder':'normal'})
shared.write_html(fig, f'inz_DE-BY-MUC')
fig.show()

In [46]:

def plot_lk_inz_per_week(*lk_namen):
    fig = go.Figure()
    for lk in lk_namen:
        lk_df = prepare_lk(lk)
        lk_df = lk_df.groupby(['year_and_week']).mean()
        fig.add_trace(go.Bar(x=lk_df.index,
                             y=lk_df['inz'],
                             name=lk, ))

    fig.update_layout(
        width=1000,
        height=500,
        title=f'Durchschnitt der Inzidenz pro Kalenderwoche'
    )
    fig.show()


plot_lk_inz_per_week('SK München', 'LK München', 'LK Tirschenreuth')

### Inzidenz Geglättet

In [47]:

def plot_lk_inz_smooth(*lk_namen, smooth=7):
    fig = go.Figure()
    for lk in lk_namen:
        lk_df = prepare_lk(lk)

        fig.add_trace(go.Scatter(x=lk_df.index,
                                 y=lk_df['inz'].rolling(smooth).mean(),
                                 mode='lines',
                                 name=lk,
                                 visible="legendonly",
                                 line=dict(width=2)))

    fig.update_layout(
        width=1000,
        height=500,
        title=f'Inzidenz geglättet ({smooth} Tage Fenster)'
    )
    fig.show()


plot_lk_inz_smooth('SK München', 'LK München', 'Berlin', 'SK Flensburg', 'LK Tirschenreuth', 'LK Regensburg',
                   'LK Miesbach', smooth=7)


### Änderung der Inzidenz

In [48]:
def plot_lk_inz_change(*lk_namen, smooth=7):
    fig = go.Figure()
    for lk in lk_namen:
        lk_df = prepare_lk(lk)

        fig.add_trace(go.Scatter(x=lk_df.index,
                                 y=lk_df['inz_dif'].rolling(smooth).mean(),
                                 mode='lines',
                                 name=lk,
                                 line=dict(width=2)))

        fig.add_trace(go.Scatter(x=lk_df.index,
                                 y=lk_df['inz_dif'],
                                 mode='markers',
                                 name=lk,
                                 marker=dict(
                                     color='grey',
                                     size=2,
                                 )))

    fig.update_layout(
        width=1000,
        height=500,
        yaxis_range=[-11,11],
        title=f'Änderung der Inzidenz Geglättet ({smooth} Tage Fenster)'
    )
    fig.show()


plot_lk_inz_change('SK München', 'Berlin', 'SK Flensburg', 'LK Tirschenreuth', 'LK Regensburg', 'LK Miesbach',
                   smooth=21)
